# Άσκηση 04 Βελτιστοποίηση kNN και SVC στο Iris με την Optuna

![](https://res.cloudinary.com/practicaldev/image/fetch/s--XpO3kV9Z--/c_imagga_scale,f_auto,fl_progressive,h_420,q_auto,w_1000/https://dev-to-uploads.s3.amazonaws.com/i/r8wwzb70006nq7hy24ct.jpeg)


Χρησιμοποιώντας την βιβλιοθήκη Optuna βρείτε τις βέλτιστες υπερπαραμέτρους για τον kNN και τα SVM στο Iris dataset.


## Optuna tutorial: *Optimize Your Optimization*

![](https://optuna.org/assets/img/optuna-logo.png) 


Μελετήστε πρώτα τα τέσσερα παραδείγματα κάτω από το ["Key Features"](https://optuna.readthedocs.io/en/stable/tutorial/index.html#key-features) της τεκμηρίωσης της Optuna.


## Βήματα

1. Ορίστε μια συνάρτηση - στόχο "objective" η οποία θα θα εκπαιδεύει τους ταξινομητές και θα επιστρέφει το μέσο τετραγωνικό σφάλμα στο test set.
2. Εντός της "objective" χρησιμοποιήστε τις μεθόδους trial.suggest_categorical, trial.suggest_int, και trial.suggest_loguniform γιά όλες τις επιλογές που πρέπει να γίνουν. Hint: ξεκινήστε με trial_suggest_categorical για το είδος του ταξινομητή, ώστε να "χωρέσουν" και οι δύο σε ένα function.
3. Βελτιστοποιήστε κάνοντας 100 δοκιμές ως εξής: 
```python
import optuna
# depending on the definition of objective
# we can create study object with either minimize or maximize
study = optuna.create_study(direction='minimize')
# start tuning for the hyper-parameters
study.optimize(objective, n_trials=100)
```



## Υπερπαράμετροι, τιμές και εύρη τιμών προς εξερεύνηση

[kNN](https://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html)

* n_neighbors: 3 με 11
* algorithm: "ball_tree", και "kd_tree"
* leaf_size: 1 με 50
* metric: "euclidean", "manhattan", "chebyshev", και "minkowski"


[SVC](https://scikit-learn.org/stable/modules/generated/sklearn.svm.SVC.html)

* C: 1e-10 με 1
* kernel: 'poly', 'rbf', 'sigmoid'
* degree: 1 με 50
* gamma: 0.001 με 10000



## Επιλογή μοντέλου

* Ποιο είναι το καλύτερο μοντέλαο kNN;
* Ποιο είναι το καλύτερο μοντέλο SVM;
* Ποιο έίναι το καλύτερο μοντέλο συνολικά;

In [ ]:
from sklearn.svm import SVC
from sklearn import datasets
from sklearn.metrics import mean_squared_error
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split


def objective(trial):

    # Load data
    iris = datasets.load_iris()
    x = iris.data
    y = iris.target
    x_train,x_test,y_train,y_test = train_test_split(x,y,test_size=0.2)
    
    # Sample hyper parameters
    classifier_name = trial.suggest_categorical("classifier", ["KNeighborsClassifier",
                                                               "SVC"])
    if classifier_name=="KNeighborsClassifier":

        # Sample hyper parameters
        n_neighbors = trial.suggest_int('n_neighbors', 3, 11)
        algorithm = trial.suggest_categorical("algorithm", 
                                              ["ball_tree",
                                                "kd_tree"])
        leaf_size = trial.suggest_int('leaf_size', 1, 50)
        metric = trial.suggest_categorical('metric', 
                                           ["euclidean","manhattan", 
                                            "chebyshev","minkowski"])
        # Construct the model
        clf = KNeighborsClassifier(n_neighbors=n_neighbors,
                               algorithm=algorithm,
                               leaf_size=leaf_size,
                               metric=metric,
                               )
    elif classifier_name=="SVC":

        # Sample hyper parameters
        C = trial.suggest_loguniform('C', 1e-10, 1)
        kernel = trial.suggest_categorical('kernel',['poly','rbf','sigmoid'])
        degree = trial.suggest_int('degree',1, 50)
        gamma = trial.suggest_loguniform('gamma',0.001,10000)

        # Construct the model
        clf = SVC(C=C, kernel=kernel, degree=degree,gamma=gamma)
    
    # Train the model
    clf.fit(x_train,y_train)

    # Evaluate the model
    y_pred_test = clf.predict(x_test)
    loss = mean_squared_error(y_test,y_pred_test)
    print("Test Score:",clf.score(x_test,y_test))
    print("Train Score:",clf.score(x_train,y_train))
    print("\n=================")
    return loss

In [ ]:
!pip install optuna

     |████████████████████████████████| 308 kB 7.4 MB/s 
     |████████████████████████████████| 80 kB 8.0 MB/s 
     |████████████████████████████████| 209 kB 44.6 MB/s 
     |████████████████████████████████| 75 kB 4.1 MB/s 
     |████████████████████████████████| 49 kB 5.2 MB/s 
     |████████████████████████████████| 111 kB 48.8 MB/s 
     |████████████████████████████████| 144 kB 57.6 MB/s 
  Created wheel for pyperclip: filename=pyperclip-1.8.2-py3-none-any.whl size=11136 sha256=b42e7674a54ce1ad5659e0db0acbaae656e6427a9b28c19209adbe397b7e4650
  Stored in directory: /root/.cache/pip/wheels/9f/18/84/8f69f8b08169c7bae2dde6bd7daf0c19fca8c8e500ee620a28
Successfully built pyperclip


In [ ]:
import optuna

# depending on the definition of objective
# we can create study object with either minimize or maximize
study = optuna.create_study(direction='minimize')

# start tuning for the hyper-parameters
study.optimize(objective, n_trials=100)

[I 2021-11-01 06:22:07,359] A new study created in memory with name: no-name-5b2ae69b-af62-4aaf-a433-126b705769d4
[I 2021-11-01 06:22:07,381] Trial 0 finished with value: 0.8 and parameters: {'classifier': 'SVC', 'C': 7.209139830340565e-09, 'kernel': 'sigmoid', 'degree': 44, 'gamma': 8625.006179740649}. Best is trial 0 with value: 0.8.
[I 2021-11-01 06:22:07,406] Trial 1 finished with value: 0.06666666666666667 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 3, 'algorithm': 'ball_tree', 'leaf_size': 28, 'metric': 'manhattan'}. Best is trial 1 with value: 0.06666666666666667.
[I 2021-11-01 06:22:07,419] Trial 2 finished with value: 2.8666666666666667 and parameters: {'classifier': 'SVC', 'C': 3.1350657380153916e-05, 'kernel': 'sigmoid', 'degree': 38, 'gamma': 0.12048471595657338}. Best is trial 1 with value: 0.06666666666666667.
[I 2021-11-01 06:22:07,436] Trial 3 finished with value: 0.03333333333333333 and parameters: {'classifier': 'SVC', 'C': 2.662898901538909e

Test Score: 0.2
Train Score: 0.36666666666666664

Test Score: 0.9333333333333333
Train Score: 0.975

Test Score: 0.03333333333333333
Train Score: 0.06666666666666667

Test Score: 0.9666666666666667
Train Score: 1.0

Test Score: 0.26666666666666666
Train Score: 0.35

Test Score: 1.0
Train Score: 0.9833333333333333

Test Score: 0.26666666666666666
Train Score: 0.35

Test Score: 0.9333333333333333
Train Score: 0.975

Test Score: 0.23333333333333334
Train Score: 0.35833333333333334

Test Score: 0.26666666666666666
Train Score: 0.35

Test Score: 0.9333333333333333
Train Score: 0.975



[I 2021-11-01 06:22:07,599] Trial 11 finished with value: 0.06666666666666667 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 9, 'algorithm': 'ball_tree', 'leaf_size': 44, 'metric': 'minkowski'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,647] Trial 12 finished with value: 0.0 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 7, 'algorithm': 'kd_tree', 'leaf_size': 26, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,672] Trial 13 finished with value: 0.0 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 7, 'algorithm': 'kd_tree', 'leaf_size': 27, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,695] Trial 14 finished with value: 0.03333333333333333 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 7, 'algorithm': 'kd_tree', 'leaf_size': 35, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,722] Trial 

Test Score: 0.9333333333333333
Train Score: 0.9833333333333333

Test Score: 1.0
Train Score: 0.9833333333333333

Test Score: 1.0
Train Score: 0.975

Test Score: 0.9666666666666667
Train Score: 0.975

Test Score: 0.9666666666666667
Train Score: 0.9666666666666667

Test Score: 1.0
Train Score: 0.9833333333333333

Test Score: 0.9333333333333333
Train Score: 0.9916666666666667



[I 2021-11-01 06:22:07,822] Trial 18 finished with value: 0.06666666666666667 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 10, 'algorithm': 'ball_tree', 'leaf_size': 38, 'metric': 'manhattan'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,842] Trial 19 finished with value: 0.0 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 9, 'algorithm': 'ball_tree', 'leaf_size': 50, 'metric': 'minkowski'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,871] Trial 20 finished with value: 0.03333333333333333 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 11, 'algorithm': 'kd_tree', 'leaf_size': 47, 'metric': 'minkowski'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,894] Trial 21 finished with value: 0.1 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 8, 'algorithm': 'kd_tree', 'leaf_size': 33, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:07,916] Tr

...

Test Score: 0.3333333333333333
Train Score: 0.3333333333333333

Test Score: 0.9
Train Score: 0.975

Test Score: 0.9666666666666667
Train Score: 0.975

Test Score: 0.7333333333333333
Train Score: 0.65

Test Score: 0.3333333333333333
Train Score: 0.425

Test Score: 0.16666666666666666
Train Score: 0.375

Test Score: 0.9333333333333333
Train Score: 0.9833333333333333

Test Score: 0.9
Train Score: 0.9916666666666667

Test Score: 0.9333333333333333
Train Score: 0.975



[I 2021-11-01 06:22:12,660] Trial 89 finished with value: 0.03333333333333333 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 8, 'algorithm': 'ball_tree', 'leaf_size': 11, 'metric': 'minkowski'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:12,684] Trial 90 finished with value: 0.0 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 7, 'algorithm': 'kd_tree', 'leaf_size': 23, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:12,709] Trial 91 finished with value: 0.06666666666666667 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 7, 'algorithm': 'kd_tree', 'leaf_size': 22, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:12,737] Trial 92 finished with value: 0.06666666666666667 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 9, 'algorithm': 'ball_tree', 'leaf_size': 47, 'metric': 'euclidean'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06

Test Score: 0.9666666666666667
Train Score: 0.975

Test Score: 1.0
Train Score: 0.975

Test Score: 0.9333333333333333
Train Score: 0.9666666666666667

Test Score: 0.9333333333333333
Train Score: 0.975

Test Score: 0.9333333333333333
Train Score: 0.9583333333333334

Test Score: 1.0
Train Score: 0.9833333333333333

Test Score: 0.9333333333333333
Train Score: 0.9666666666666667

Test Score: 0.9666666666666667
Train Score: 0.975



[I 2021-11-01 06:22:12,875] Trial 97 finished with value: 0.03333333333333333 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 10, 'algorithm': 'kd_tree', 'leaf_size': 34, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:12,920] Trial 98 finished with value: 0.03333333333333333 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 8, 'algorithm': 'ball_tree', 'leaf_size': 40, 'metric': 'minkowski'}. Best is trial 5 with value: 0.0.
[I 2021-11-01 06:22:12,947] Trial 99 finished with value: 0.1 and parameters: {'classifier': 'KNeighborsClassifier', 'n_neighbors': 6, 'algorithm': 'kd_tree', 'leaf_size': 25, 'metric': 'chebyshev'}. Best is trial 5 with value: 0.0.


Test Score: 0.9666666666666667
Train Score: 0.9916666666666667

Test Score: 0.9666666666666667
Train Score: 0.9916666666666667

Test Score: 0.9
Train Score: 0.9833333333333333

